In [1]:
import asyncio
import itertools
import sys
import os
import pathlib
base_path_str = '.'
base_path = pathlib.Path(base_path_str)
sys.path.append(base_path_str)

import huggingface_hub as hfh
import pandas as pd
import timm
from determined.experimental import client
from tqdm.notebook import tqdm
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
sns.set_theme(style="darkgrid")
sns.set(rc={"figure.figsize":(10, 10)})


import workspaces

pd.set_option('display.max_rows', 5000)
pd.set_option('display.max_columns', 500)

All relevant `timm` models:

In [2]:
all_timm_models_df = pd.read_feather(base_path.joinpath('models/selected_timm_models.feather'))
all_timm_models_df

model    top1  top1_err    top5  top5_err  param_count  \
0    ig_resnext101_32x48d  85.436    14.564  97.576     2.424       828.41   
1  beit_large_patch16_512  88.602    11.398  98.656     1.344       305.67   
2               resnet152  82.818    17.182  96.132     3.868        60.19   
3         efficientnet_b0  77.700    22.300  93.532     6.468         5.29   

   img_size  crop_pct interpolation  \
0       224     0.875      bilinear   
1       512     1.000       bicubic   
2       224     0.950       bicubic   
3       224     0.875       bicubic   

                              state_dict_path  
0            ig_resnext101_32x48-3e41cc8a.pth  
1  beit_large_patch16_512_pt22k_ft22kto1k.pth  
2                  resnet152_a1h-dc400468.pth  
3             efficientnet_b0_ra-3dd342df.pth

Get results from cluster

In [3]:
master = ! echo $GCP_T4X4_MASTER
master = master[0]
client.login(master=master, user='determined', password='')

In [4]:
w = workspaces.Workspace(workspace_name='DeepSpeed',
                         master_url=master,
                         username='determined',
                         password='')

Separating autotuning results from those found with the flops profiler:

In [5]:
all_project_names = w.get_all_project_names()
autotuning_project_names = [name for name in all_project_names if name.split('.')[-1] == 'autotuning']
flops_profiler_project_names = [name for name in all_project_names if name.split('.')[-1] == 'flops_profiler']

In [6]:
flops_profiler_results_df = w.get_trial_best_val_results_df(flops_profiler_project_names)
flops_profiler_results_df

Getting Experiments from resnet152.flops_profiler: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  5.22it/s]
Getting Trials from resnet152.flops_profiler: 100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 20.19it/s]
Getting Experiments from beit_large_patch16_512.flops_profiler: 100%|████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  3.72it/s]
Getting Trials from beit_large_patch16_512.flops_profiler: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████| 3/3 [00:00<00:00, 20.66it/s]
Getting Experiments from ig_resnext101_32x48d.flops_profiler: 100%|██████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:00<00:00,  9.32it/s]
Getting Trials from ig_resnext101_32x48d

FLOPS_per_gpu            checkpoint_path_prefix   dataset_name  \
39389   6.290000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
39462   6.400000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
40396   5.900000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
39387   3.340000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
39455   3.170000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
40395   3.160000e+12  shared_fs/ensembles/state_dicts/  mini_imagenet   
39408   5.449200e+11  shared_fs/ensembles/state_dicts/  mini_imagenet   
39459   5.717100e+11  shared_fs/ensembles/state_dicts/  mini_imagenet   
40812   4.995700e+11  shared_fs/ensembles/state_dicts/  mini_imagenet   

       ds_config_flops_profiler_detailed  ds_config_flops_profiler_enabled  \
39389                               True                              True   
39462                               True                              True   
40396                               True                              True   
39387                               True                              True   
39455                               True                              True   
40395                               True                              True   
39408                               True                              True   
39459                               True                              True   
40812                               True                              True   

       ds_config_flops_profiler_module_depth  \
39389                                     -1   
39462                                     -1   
40396                                     -1   
39387                                     -1   
39455                                     -1   
40395                                     -1   
39408                                     -1   
39459                                     -1   
40812                                     -1   

                    ds_config_flops_profiler_output_file  \
39389  /run/determined/workdir/flops_profiler_output.txt   
39462  /run/determined/workdir/flops_profiler_output.txt   
40396  /run/determined/workdir/flops_profiler_output.txt   
39387  /run/determined/workdir/flops_profiler_output.txt   
39455  /run/determined/workdir/flops_profiler_output.txt   
40395  /run/determined/workdir/flops_profiler_output.txt   
39408  /run/determined/workdir/flops_profiler_output.txt   
39459  /run/determined/workdir/flops_profiler_output.txt   
40812  /run/determined/workdir/flops_profiler_output.txt   

       ds_config_flops_profiler_profile_step  \
39389                                      5   
39462                                      5   
40396                                      5   
39387                                      5   
39455                                      5   
40395                                      5   
39408                                      5   
39459                                      5   
40812                                      5   

       ds_config_flops_profiler_top_modules  ds_config_fp16_enabled  \
39389                                     1                    True   
39462                                     1                    True   
40396                                     1                    True   
39387                                     1                    True   
39455                                     1                    True   
40395                                     1                    True   
39408                                     1                    True   
39459                                     1                    True   
40812                                     1                    True   

       ds_config_fp16_initial_scale_power  \
39389                                   8   
39462                                   8   
40396                                   8   
39387                                   8

Due to DS bugs, for all *autotuning* trials the `latency` is in $\mu{\rm s}$, the `throughput` is in records/${\rm ms}$, and the `FLOPS_per_gpu` also has weird units.  Add columns with fixes everywhere so that all time units are in seconds.

In [8]:
autotuning_results_df = w.get_trial_best_val_results_df(autotuning_project_names)
autotuning_results_df.latency /= 10 ** 6
autotuning_results_df.throughput *= 10 ** 3
autotuning_results_df.FLOPS_per_gpu *= 10 ** 6
autotuning_results_df

Getting Experiments from efficientnet_b0.autotuning: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:01<00:00,  1.03s/it]
Getting Trials from efficientnet_b0.autotuning: 100%|████████████████████████████████████████████████████████████████████████████████████████████████████████| 324/324 [00:05<00:00, 62.44it/s]
Getting Experiments from beit_large_patch16_512.autotuning: 100%|████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:01<00:00,  1.19s/it]
Getting Trials from beit_large_patch16_512.autotuning: 100%|█████████████████████████████████████████████████████████████████████████████████████████████████| 324/324 [00:05<00:00, 59.58it/s]


FLOPS_per_gpu  autotuning_enabled  autotuning_end_profile_step  \
39452   6.401901e+12                True                            5   
39509   6.906425e+12                True                            5   
39552   5.862476e+12                True                            5   
39398   5.994374e+12                True                            5   
39482   6.489634e+12                True                            5   
39412   6.288334e+12                True                            5   
39487   6.920391e+12                True                            5   
39554   5.816515e+12                True                            5   
39399   6.211372e+12                True                            5   
39556   6.000917e+12                True                            5   
39411   5.967198e+12                True                            5   
39559   5.337804e+12                True                            5   
39400   6.017252e+12                True                            5   
39561   5.860454e+12                True                            5   
39401   6.121376e+12                True                            5   
39490   6.943971e+12                True                            5   
39562   5.928899e+12                True                            5   
39409   5.977346e+12                True                            5   
39563   5.163321e+12                True                            5   
39410   6.390872e+12                True                            5   
39564   5.963790e+12                True                            5   
39464   6.182823e+12                True                            5   
39515   7.193368e+12                True                            5   
39427   6.242848e+12                True                            5   
39517   6.932499e+12                True                            5   
39446   5.225188e+12                True                            5   
39523   6.805725e+12                True                            5   
39439   6.213724e+12                True                            5   
39450   6.193791e+12                True                            5   
39538   6.897341e+12                True                            5   
39447   5.269598e+12                True                            5   
39545   6.739425e+12                True                            5   
39598   5.763461e+12                True                            5   
39443   5.733002e+12                True                            5   
39600   5.846888e+12                True                            5   
39435   5.792461e+12                True                            5   
39603   5.940275e+12                True                            5   
39454   5.887725e+12                True                            5   
39520   6.573578e+12                True                            5   
39632   6.086033e+12                True                            5   
39991   6.928657e+12                True                            5   
40371   5.891920e+12                True                            5   
39622   5.511652e+12                True                            5   
39992   6.853936e+12                True                            5   
40372   5.884205e+12                True                            5   
39625   6.163023e+12                True                            5   
39993   7.388272e+12                True                            5   
40376   6.049703e+12                True                            5   
39670   6.234384e+12                True                            5   
39995   6.988381e+12                True                            5   
40377   6.224335e+12                True                            5   
39624   5.711440e+12                True                            5   
39996   6.249764e+12                True                            5   
40379   4.982976e+12                True                         

There is some weird issue going on w/ reported tuner types.  The `ds_config_autotuning_tuner_type` field is the tuner type specified in the `yaml` config and should be the type used during autotuning.  The `autotuning_tuner_type` field, however, is read out of the actual DS autotuner output and does not always match. Very weird. Similar inconsistencies also happen for the autotuning metric.

See [this Trial](http://104.196.135.13:8080/det/experiments/25858/logs?searchText=tuner_type) for an example.  The conflict can be seen to be within DS by comparing the logs and the checkpoint info, e.g.

In [9]:
conflicts = {}
for arg in ('tuner_type', 'metric', 'fast'):
    conflict_mask = ~(autotuning_results_df[f'autotuning_{arg}'] == autotuning_results_df[f'ds_config_autotuning_{arg}'])
    conflicts[arg] = autotuning_results_df[conflict_mask]

# Check the number of conflicts:
{k: len(v) for k, v in conflicts.items()}



{'tuner_type': 145, 'metric': 114, 'fast': 145}

Visualizing one example:

In [10]:
conflicts['tuner_type'][['ds_config_autotuning_tuner_type', 'autotuning_tuner_type']]

ds_config_autotuning_tuner_type autotuning_tuner_type
39860                      gridsearch                random
40609                      gridsearch           model_based
39841                     model_based            gridsearch
39828                     model_based            gridsearch
39831                      gridsearch           model_based
40637                     model_based            gridsearch
40620                      gridsearch           model_based
40236                     model_based                random
40223                     model_based                random
40219                          random           model_based
40222                          random           model_based
40235                          random           model_based
40631                          random           model_based
39846                     model_based                random
40628                          random           model_based
39852                          random           model_based
39854                          random           model_based
40650                          random            gridsearch
39862                          random            gridsearch
40242                          random            gridsearch
40634                      gridsearch                random
39856                      gridsearch                random
39871                     model_based            gridsearch
40257                     model_based            gridsearch
40649                      gridsearch           model_based
40255                      gridsearch           model_based
40258                      gridsearch           model_based
40262                      gridsearch           model_based
40662                     model_based                random
39894                     model_based                random
40269                          random           model_based
40274                          random           model_based
40670                          random           model_based
40276                     model_based                random
40676                          random           model_based
40671                     model_based                random
40278                          random            gridsearch
39906                          random            gridsearch
40291                          random            gridsearch
40694                          random            gridsearch
40472                     model_based            gridsearch
40493                      gridsearch           model_based
40514                      gridsearch           model_based
39716                          random           model_based
40069                     model_based                random
39713                          random           model_based
39712                          random           model_based
40078                     model_based                random
40092                          random           model_based
40530                     model_based                random
40503                          random           model_based
40499                          random            gridsearch
39744                          random            gridsearch
39732                      gridsearch                random
40105                      gridsearch                random
40089                      gridsearch                random
40087                      gridsearch                random
40104                      gridsearch                random
40658                          random            gridsearch
40511                          random            gridsearch
40495                          random            gridsearch
39723                      gridsearch           model_based
40100                      gridsearch           model_based
40545                      gridsearch           model_based
40210                     model_based            gridsearch
40498                      gridsearch         

They are not all subsets of each other:

In [11]:
for a, b in itertools.product(conflicts.values(), conflicts.values()):
    if a is not b:
        print(a.index.isin(b.index).all())

False
True
True
True
True
False


Use the reported values (non-`ds_config`) values everywhere and continue:

In [12]:
all_results_df = pd.concat([autotuning_results_df, flops_profiler_results_df])

Create a helper autotuning column

In [13]:
all_results_df['autotuning'] = ~all_results_df.autotuning_enabled.isnull()

In [14]:
plots_dir = base_path.joinpath('plots')

def create_masks(df, metric, model_name, tuner_type, fast):
    model_mask = df.model_name == model_name
    throughput_mask = df.autotuning_metric == metric
    fast_mask = df.autotuning_fast == fast
    tuner_type_mask = df.autotuning_tuner_type == tuner_type
    baseline_mask = model_mask & (df.autotuning_metric.isnull())
    mask_without_baseline = model_mask & throughput_mask & fast_mask & tuner_type_mask
    mask_with_baseline = mask_without_baseline | baseline_mask
    
    return baseline_mask, mask_without_baseline, mask_with_baseline 

def get_param_count(model_name):
    params = all_timm_models_df[all_timm_models_df.model==model_name].param_count.iloc[0]
    return params

def create_and_save_plot(df, metric, model_name, tuner_type, fast):
    baseline_mask, mask_without_baseline, mask_with_baseline = create_masks(df, metric, model_name, tuner_type, fast)
    masked_df = df[mask_with_baseline]
    
    fig, ax = plt.subplots(1, 1)
    exp_desc = f"{'fast ' if fast else ''}{tuner_type} {model_name}"
    title_str = exp_desc + f' ({get_param_count(model_name)}M. params.)'
    sns.lineplot(x='slots_per_trial', 
                 y=metric, 
                 hue='autotuning', 
                 data=masked_df, 
                 markers=True, 
                 ci=68,
                 ax=ax).set(title=f"{model_name} {tuner_type} {'fast' if fast else ''}")
    autotuning_means = masked_df.groupby('slots_per_trial').mean()[metric]
    baselines = df[baseline_mask].groupby('slots_per_trial').mean()[metric]
    ratios = autotuning_means / baselines
    for ((slots, mean), (_, ratio)) in zip(autotuning_means.iteritems(), ratios.iteritems()):
        desc = f'{mean:.2e}'
        if ratio == ratio: # funky nan check
            desc += f'  ({ratio:.2f}x)'
        ax.text(slots, mean, desc)
    if baselines.any():
        for slots, mean in baselines.iteritems():
            desc = f'{mean:.2e}'
            ax.text(slots, mean, desc)
            
    plot_subdir = plots_dir.joinpath(metric)
    os.makedirs(plot_subdir, exist_ok=True)
    file_str = '_'.join(exp_desc.split()) + f'_{metric}.png'
    save_path = plot_subdir.joinpath(file_str)
    fig.figure.savefig(save_path, dpi=512)

In [15]:
def no_nans(x):
    for item in x:
        if item != item:
            return False
    return True

def non_nans_iter(x):
    for item in x:
        if item != item:
            continue
        yield item
        
def non_nans_product(*args):
    prod = itertools.product(*(non_nans_iter(x) for x in args))
    return prod

In [ ]:
for combo in non_nans_product(all_results_df.autotuning_metric.unique(),
                               all_results_df.model_name.unique(),
                               all_results_df.autotuning_tuner_type.unique(),
                               all_results_df.autotuning_fast.unique()):
    create_and_save_plot(all_results_df, *combo)
    

Tables:

Isolate all trials which have a baseline to compare to, then compute the relative improvement:

In [23]:
baseline_model_names = flops_profiler_results_df.model_name.unique()

In [24]:
results_with_baseline_df = autotuning_results_df[autotuning_results_df.model_name.isin(baseline_model_names)].copy()

In [25]:
def get_baseline_and_ratio(df, baseline_df):
    baseline = []
    ratio = []
    for _, val in df.iterrows():
        model_mask = baseline_df.model_name == val.model_name
        slot_mask = baseline_df.slots_per_trial == val.slots_per_trial
        masked_baseline_df = baseline_df[model_mask & slot_mask]
        baseline_metric = masked_baseline_df[val.autotuning_metric].values
        val_metric = val[val.autotuning_metric]
        baseline.append(baseline_metric)
        ratio.append(val_metric / baseline_metric)
    baseline = np.concatenate(baseline)
    ratio = np.concatenate(ratio)
    return baseline, ratio

In [26]:
results_with_baseline_df['baseline'], results_with_baseline_df['ratio'] = get_baseline_and_ratio(results_with_baseline_df, flops_profiler_results_df)

Create a multi-index dataframe summarizing results.

In [28]:
ratio_summary = results_with_baseline_df.groupby(['autotuning_metric', 'model_name', 'autotuning_tuner_type', 'autotuning_fast', 'slots_per_trial'])['ratio'].mean()

Slice in various ways with `groupby`:

Global:

In [30]:
ratio_summary.groupby(level=0).mean()

autotuning_metric
FLOPS_per_gpu    1.628147
latency          1.060911
throughput       1.663369
Name: ratio, dtype: float64

One more level of detail:

In [32]:
for a in range(1, 5):
    print(ratio_summary.groupby(level=(0, a)).mean(), 80 * '-', sep='\n')

autotuning_metric  model_name            
FLOPS_per_gpu      beit_large_patch16_512    2.448826
                   efficientnet_b0           1.421646
                   resnet152                 1.013970
latency            beit_large_patch16_512    1.067912
                   efficientnet_b0           1.024686
                   resnet152                 1.090135
throughput         beit_large_patch16_512    2.489719
                   efficientnet_b0           1.479497
                   resnet152                 1.020890
Name: ratio, dtype: float64
--------------------------------------------------------------------------------
autotuning_metric  autotuning_tuner_type
FLOPS_per_gpu      gridsearch               1.607662
                   model_based              1.622163
                   random                   1.654617
latency            gridsearch               1.062146
                   model_based              1.060433
                   random                   1.060155
thro

Fast mode isn't much faster:

In [33]:
results_with_baseline_df[results_with_baseline_df.autotuning_fast].wall_clock_time.mean()

859.5790279813278

In [34]:
results_with_baseline_df[~results_with_baseline_df.autotuning_fast].wall_clock_time.mean()

887.0996187408165